### Syntax similarity

In [7]:
import spacy

In [20]:
import spacy
nlp = spacy.load("en_core_web_sm")

In [5]:
import pandas as pd

data = pd.read_csv('claim_reviews_en.csv')

In [17]:
import pickle

with open ( "preprocessed_tweets.pickle", "rb" ) as f:
    tweets = pickle.load(f)

In [ ]:
pos_map = {}
for i, txt in enumerate(data.claim_text):
    doc = nlp(txt)
    pos_list = []
    for token in doc:
        pos_list.append(token.pos_)
    pos_map[i] = pos_list

In [21]:
pos_map = {}
for i, txt in enumerate(tweets):
    doc = nlp(txt)
    pos_list = []
    for token in doc:
        pos_list.append(token.pos_)
    pos_map[i] = pos_list

In [22]:
import pickle

with open ( "pos_map.pkl", "wb" ) as f:
    pickle.dump( pos_map, f )

In [1]:
import pickle

with open ( "pos_map.pkl", "rb" ) as f:
    pos_map = pickle.load(f)

In [24]:
from nltk.util import ngrams

list(ngrams(pos_map[100], 3)) 

[('SCONJ', 'AUX', 'PRON'),
 ('AUX', 'PRON', 'PART'),
 ('PRON', 'PART', 'DET'),
 ('PART', 'DET', 'ADJ'),
 ('DET', 'ADJ', 'NOUN'),
 ('ADJ', 'NOUN', 'PRON'),
 ('NOUN', 'PRON', 'NUM'),
 ('PRON', 'NUM', 'ADP'),
 ('NUM', 'ADP', 'DET'),
 ('ADP', 'DET', 'ADJ'),
 ('DET', 'ADJ', 'NOUN'),
 ('ADJ', 'NOUN', 'ADP'),
 ('NOUN', 'ADP', 'DET'),
 ('ADP', 'DET', 'PROPN'),
 ('DET', 'PROPN', 'CCONJ'),
 ('PROPN', 'CCONJ', 'DET'),
 ('CCONJ', 'DET', 'NOUN'),
 ('DET', 'NOUN', 'NOUN'),
 ('NOUN', 'NOUN', 'NOUN'),
 ('NOUN', 'NOUN', 'VERB'),
 ('NOUN', 'VERB', 'DET'),
 ('VERB', 'DET', 'ADJ'),
 ('DET', 'ADJ', 'NOUN'),
 ('ADJ', 'NOUN', 'PUNCT'),
 ('NOUN', 'PUNCT', 'ADJ'),
 ('PUNCT', 'ADJ', 'NOUN'),
 ('ADJ', 'NOUN', 'ADP'),
 ('NOUN', 'ADP', 'PRON'),
 ('ADP', 'PRON', 'NOUN'),
 ('PRON', 'NOUN', 'ADP'),
 ('NOUN', 'ADP', 'PRON'),
 ('ADP', 'PRON', 'NOUN'),
 ('PRON', 'NOUN', 'SCONJ'),
 ('NOUN', 'SCONJ', 'DET'),
 ('SCONJ', 'DET', 'NOUN'),
 ('DET', 'NOUN', 'NOUN'),
 ('NOUN', 'NOUN', 'ADV'),
 ('NOUN', 'ADV', 'PRON'),
 ('ADV', '

In [25]:
def syntax_similarity(trigram_map,query_index):
    similarities = []
    for i in range(len(trigram_map)):
        if i != query_index:
            trigram_map[i], common = trigram_map[i][:], [ e for e in trigram_map[query_index] if e in trigram_map[i] and (trigram_map[i].pop(trigram_map[i].index(e)))]
            commons = len(common)
            for tri in common:
                if "VERB" in tri:
                    commons += 1
            min_count = min(len(trigram_map[query_index]),len(trigram_map[i]))
            if min_count == 0:
                similar = 0
            else:
                similar = min(commons/min_count,1)
        else:
            similar = 1

        ref_indices = [i for i, x in enumerate(pos_map[query_index]) if x == "PUNCT"]
        comp_indices = [i for i, x in enumerate(pos_map[i]) if x == "PUNCT"]
        ref_indices.append(len(pos_map[query_index]))
        comp_indices.append(len(pos_map[i]))
        def sen_lens(index_list):
            result = []
            result.append(index_list[0])
            if len(index_list) > 1:
                for i in range(1,len(index_list)):
                    result.append(index_list[i] - index_list[i-1])
            return result
        ref_lens = sen_lens(ref_indices)
        comp_lens = sen_lens(comp_indices)
        for i in range(min(len(ref_lens),len(comp_lens))):
            if ref_lens[i] != comp_lens[i]:
                similar *= 1 / abs(ref_lens[i]-comp_lens[i])
        if len(ref_lens) != len(comp_lens):
            similar *= 0.05 / abs(len(ref_lens)-len(comp_lens))
        similarities.append(similar**0.1)

    return similarities

In [26]:
trigram_map = {}
for i in range(len(pos_map)):
    trigram_map[i] = list(ngrams(pos_map[i], 3))

In [27]:
import numpy as np
np.argsort(similarities)[-10:]

NameError: name 'similarities' is not defined

In [11]:
data.claim_text[0]

'Ratan Tata Says, If The Death Of 65 Soldiers Increases The Popularity Of A Prime Minister, Then Nobody Can Save This Country'

In [12]:
data.claim_text[5429]

'No, Samajwadi Party Did Not Promise Jobs To All Muslim Youts If the Won Election, The Viral Claim Is False'

In [42]:
## word2vec

In [39]:
model2 = gensim.models.Word2Vec(list(pos_map.values()), min_count = 1, vector_size = 100,
                                             window = 5, sg = 2)

In [40]:
print("Cosine similarity between 'NOUN' " +
                 "and 'PROPN': ",
      model2.wv.similarity('NOUN', 'PROPN'))

Cosine similarity between 'NOUN' and 'PROPN' - CBOW :  0.5716491


In [41]:
print("Cosine similarity between 'NOUN' " +
                 "and 'PUNCT' - CBOW : ",
      model2.wv.similarity('NOUN', 'PUNCT'))

Cosine similarity between 'NOUN' and 'PUNCT' - CBOW :  0.6224729


In [21]:
## Look into specific tags, like nouns and verbs

In [28]:
simple_pos_map = {}
for k, v in pos_map.items():
    tmp = [x if x not in ['PRON','PROPN'] else 'NOUN' for x in v]
    tmp = [x if x != 'CCONJ' else 'SCONJ' for x in tmp]
    simple_pos_map[k] = [x if x not in ['ADP','PART'] else 'ADV' for x in tmp]

In [29]:
simple_trigram_map = {}
for i in range(len(simple_pos_map)):
    simple_trigram_map[i] = list(ngrams(simple_pos_map[i], 3))

In [30]:
similarity_matrix = []
for i in range(500):
    similarities = syntax_similarity(trigram_map,0)
    simple_similarities = syntax_similarity(simple_trigram_map,0)
    weighed_similarities = [(g + h) / 2 for g, h in zip(similarities, simple_similarities)]
    similarity_matrix.append(weighed_similarities)

In [31]:
len(similarity_matrix[0])

9390

In [14]:
import pickle

with open ( "similarity_matrix_rasmus.pkl", "wb" ) as f:
    pickle.dump( similarity_matrix, f )

In [48]:
similarities = syntax_similarity(trigram_map,5)

In [49]:
simple_similarities = syntax_similarity(simple_trigram_map,5)

In [50]:
weighed_similarities = [(g + h) / 2 for g, h in zip(similarities, simple_similarities)]

In [51]:
import numpy as np
np.argsort(weighed_similarities)[-10:]

array([6717,  736, 6128, 9024, 3065, 8921, 6438, 4023, 5730,    5],
      dtype=int64)

In [47]:
tweets[5]

'insider at just sent me these internal emails... wtf??\n\n$GME $NOK $BB $AMC'

In [52]:
tweets[5730]

'Officer Who Shot And Killed Daunte Wright Was 26-Year-Veteran, Was Involved In Another Fatal Police Shooting In 2019'

In [53]:
tweets[4023]

'John Mayer Just Dropped His New Album "Sob Rock", Let\'s Break It Down'

In [55]:
tweets[6438]

'What if Rasputin DIDN’T shoot the Traveller….? 😜'

In [141]:
data.claim_text[0]

'Ratan Tata Says, If The Death Of 65 Soldiers Increases The Popularity Of A Prime Minister, Then Nobody Can Save This Country'

In [142]:
data.claim_text[18004]

"Jim Carrey Said 'Hollywood Elites Eat Whole Babies For Christmas' -'The More They Suffer-The Better They Taste'"

In [16]:
trigram_map

{0: [('PROPN', 'PROPN', 'VERB'),
  ('PROPN', 'VERB', 'PUNCT'),
  ('VERB', 'PUNCT', 'SCONJ'),
  ('PUNCT', 'SCONJ', 'DET'),
  ('SCONJ', 'DET', 'NOUN'),
  ('DET', 'NOUN', 'ADP'),
  ('NOUN', 'ADP', 'NUM'),
  ('ADP', 'NUM', 'NOUN'),
  ('NUM', 'NOUN', 'VERB'),
  ('NOUN', 'VERB', 'DET'),
  ('VERB', 'DET', 'NOUN'),
  ('DET', 'NOUN', 'ADP'),
  ('NOUN', 'ADP', 'DET'),
  ('ADP', 'DET', 'PROPN'),
  ('DET', 'PROPN', 'PROPN'),
  ('PROPN', 'PROPN', 'PUNCT'),
  ('PROPN', 'PUNCT', 'ADV'),
  ('PUNCT', 'ADV', 'PRON'),
  ('ADV', 'PRON', 'AUX'),
  ('PRON', 'AUX', 'VERB'),
  ('AUX', 'VERB', 'DET'),
  ('VERB', 'DET', 'NOUN')],
 1: [('DET', 'NOUN', 'PRON'),
  ('NOUN', 'PRON', 'VERB'),
  ('PRON', 'VERB', 'AUX'),
  ('VERB', 'AUX', 'PART'),
  ('AUX', 'PART', 'VERB'),
  ('PART', 'VERB', 'ADP'),
  ('VERB', 'ADP', 'DET'),
  ('ADP', 'DET', 'PROPN'),
  ('DET', 'PROPN', 'PROPN'),
  ('PROPN', 'PROPN', 'PROPN')],
 2: [('PROPN', 'PROPN', 'AUX'),
  ('PROPN', 'AUX', 'PART'),
  ('AUX', 'PART', 'VERB'),
  ('PART', 'VERB', 'A

In [17]:
strong_templates = {}
for trigrams in trigram_map.values():
    for trigram in trigrams:
        strong_templates[trigram] = strong_templates.get(trigram,0) + 1

In [19]:
dict(sorted(strong_templates.items(), key=lambda item: item[1],reverse=True))

{('PROPN', 'PROPN', 'PROPN'): 16829,
 ('NOUN', 'ADP', 'PROPN'): 12661,
 ('ADP', 'DET', 'NOUN'): 10111,
 ('NOUN', 'ADP', 'DET'): 9828,
 ('DET', 'NOUN', 'ADP'): 8743,
 ('PROPN', 'PROPN', 'VERB'): 8301,
 ('NOUN', 'ADP', 'NOUN'): 8014,
 ('ADP', 'PROPN', 'PROPN'): 7890,
 ('DET', 'ADJ', 'NOUN'): 7879,
 ('VERB', 'DET', 'NOUN'): 7748,
 ('PROPN', 'PROPN', 'PUNCT'): 7536,
 ('ADJ', 'NOUN', 'ADP'): 6994,
 ('NOUN', 'PUNCT', 'PUNCT'): 6155,
 ('NOUN', 'NOUN', 'ADP'): 5662,
 ('AUX', 'VERB', 'ADP'): 5645,
 ('NOUN', 'VERB', 'ADP'): 5595,
 ('ADJ', 'NOUN', 'PUNCT'): 5507,
 ('ADP', 'DET', 'PROPN'): 5361,
 ('VERB', 'ADP', 'DET'): 5300,
 ('NOUN', 'NOUN', 'PUNCT'): 5169,
 ('VERB', 'ADP', 'PROPN'): 4943,
 ('PROPN', 'ADP', 'PROPN'): 4781,
 ('VERB', 'PROPN', 'PROPN'): 4652,
 ('NOUN', 'AUX', 'VERB'): 4625,
 ('ADP', 'PROPN', 'PUNCT'): 4606,
 ('VERB', 'NOUN', 'ADP'): 4510,
 ('ADP', 'ADJ', 'NOUN'): 4288,
 ('ADP', 'DET', 'ADJ'): 4248,
 ('DET', 'PROPN', 'PROPN'): 4233,
 ('ADP', 'NOUN', 'ADP'): 4180,
 ('PROPN', 'PROPN'

In [24]:
word_map = {}
for i, txt in enumerate(data.claim_text):
    doc = nlp(txt)
    word_list = []
    for token in doc:
        word_list.append(token.text)
    word_map[i] = word_list

In [25]:
for k, trigrams in trigram_map.items():
    for i, trigram in enumerate(trigrams):
        if trigram == ('PROPN', 'PROPN', 'PUNCT'):
            print(word_map[k][i],word_map[k][i+1],word_map[k][i+2])

Prime Minister ,
Safe Ticket ,
House Speaker ]
Majority Leader ]
New Jersey ,
Femi Fani -
Democratic Party (
Progressives Congress (
Assembly Elections .
Tamil Nadu .
Emergency Department (
Single Market .
Uttar Pradesh ,
Cures Autism ,
Activity Restrictions ”
Use Authorization .
Hillary Clinton "
Donald Trump )
Luv Sinha ,
Shatrughan Sinha ,
Sanjiv Bhatt .
Laurance Rockefeller ,
D. Rockefeller ,
Chester Bennington .
Bill Gates ,
Alexandria Ocasio -
Donald Trump ,
Thousand Currents ,
Global Network .
cinchona bark .
Hillary Clinton "
Bill Gates -
Muslim Judge (
Rasmussen Poll ,
Approval Rating .
kabr khudegi&quot ;
New Jersey .
Republic Day .
Lai Mohammed ,
United States ,
United Kingdom ,
quot;John Barron.&quot ;
Jersey City ,
Capital Ethiopia ,
Mitch McConnell ,
Donald Trump ,
Walkout Day "
Responsibility Act (
Oyo State -
Alexandria Ocasio -
Universities Commission ,
Najat Vallaud -
White House —
Islamic Cooperation (
sein Bitcoin -
Paul Ryan )
Space Force .
Christopher Lloyd ,
quot

Greta Thunberg ,
Mahashay Dharampal ,
Kamala Harris ,
Donald Trump “
Tammy Baldwin --
Corruption Investigation .
Care Act "
Donald Barr ,
Bill Barr ,
Vietnam War .
Alexandria Ocasio -
Tupac Shakur )
Elisa Granato ,
War II .
North Carolina .
Delhi Riots .
CDC Admits :
Rome Ga ...
Heitkamp High -
Abortion Ban .
Christmas Eve .
George Soros .
quot;will fall&quot ;
Monetary Fund (
Uttar Pradesh .
Assam Bachao ”
Assam Congress ,
Obama Admin .
Mahlon Mitchell "
Michael Bennet )
Taj Mahal ,
Jonathan Van -
West Virginia .
West Virginia ,
COVID-19 pandemic .
Potassium Chloride ,
States Senate .
States Senate .
Regulatory Reform (
Fire Safety )
Bill Clinton :
Meghan Markle '
Brett Kavanaugh "
Ann Landers :
Alexandria Ocasio -
Eid al -
Klux Klan ,
Donald Trump )
Jimmy Carter .
Washington D.C. ,
St. Louis ,
New Orleans ,
Donald Trump ,
National Anthem "
Spangled Banner "
Bombshell Claim :
Shiraz Balsara ,
Shiraz Bulsara .
West Bengal .
Hillary Clinton "
Trade Agreement )
Trade Organization …
South

charakter intencjonalny ,
Tim Kaine "
T. Thompson ,
Henry Kissinger .
South Carolina .
Yusuf Buhari ,
Muhammadu Buhari ,
Research Vessel ”
WhatsApp Gold .
D. Eisenhower ,
Ronald Reagan ,
Health Organization .
Ted Nugent ,
Scott Baio ,
National Convention .
Homeland Security .
Campus Journalists (
UCJ UNILORIN )
Andhra Pradesh .
White Supremacy ,
Big Payback "
Clint Eastwood ,
Dr. Phil ,
NC Republicans “
North Carolinians .
Tokyo Olympics .
Steven Chu ,
Andhra Pradesh .
Sonia Sotomayor .
Joe Biden .
Willie McCovey ,
Dow Joans (
TREMENDOUS SPEED !
Vaccination Identification .
Uttar Pradesh .
personas hacen “
Mary Trump ,
Supreme Court .
North Dakota ,
Republic Day .
First Look '
Magna Carta .
Patrick Star .
Car Accident ,
David Hogg .
Bob Dole ,
Mahatma Gandhi .
Medicines Agency (
Rick Scott "
Management Commission (
Oyo State .
Dream Act ,
United States ,
Justice Department .
Bermuda Triangle .
Nana Akufo -
South Bend ,
Medicines Agency (
Pacific Partnership "
West Bengal ,
Customs Enfo

Benin Republic .
San Francisco .
Joe Biden ,
quot;good friend.&quot ;
Mandir chahiye ,
Andrew Cuomo .
Defense Forces (
Barrier Reef ,
Ronald Reagan "
Enoch Adeboye ,
Foundation Hospital ,
Rex Ryan "
New York .
Guantanamo Bay .
United States ,
David Cameron .
Tokyo Olympics .
Doug Jones "
Benz G -
Muslim Brotherhood .
Muslim Brotherhood .
Camera Abortion '
Gator Bait ”
Corruption Investigation .
Industrial Average "
Saudi Arabia .
West Bengal .
Alabama Walmart .
Orange County “
Insurance Program "
San Diego .
Amelia Bassano ,
Em Over "
President Akufo -
Lordina Mahama .
dharmastato Jayah .
Barack Obama .
Sterilization Three -
Fall River ,
West Virginia )
Jeff Denham ,
Bhabua Nagar ;
National Committee ,
Mike Tyson ,
Animal Blood ,
American Party "
Omar Mateen "
Typhoon Odette .
Aloe Vera ,
Jacob Blake ,
Peppermint Alfredo "
Drug Administration (
New York ,
Dairy Products !
Hillary Clinton "
Deports Muslims ;
Joe Biden "
Iraq War ,
Straight Days .
Rick Scott "
West Virginia "
da Europa .

Management Council (
Territory Administration (
Manik Moitra ,
Cooch Behar ,
West Bengal .
Frozen Dessert ”
Sen. Rob )
Scraps Vaccine ,
Kassio Nunes ]
Cesare Battisti .
Hillary Clinton "
Appreciation Day .
President Trump "
Donald Trump .
Tom McClintock ,
Sad News ,
U.S. Capitol ,
National Guard .
Pearl Harbor .
Morning Images ,
North Korea "
David Rockefeller ,
Ajmal Kasab .
West Virginia .
West Virginia ,
Donald Trump “
Middle East .
Colin Powell ,
Tim Kaine "
Mount Sterling ,
ne demokratiji '
Ayatollah Khamenei .
Phil Bredesen "
Convict Trump ”
Hurricane Florence :
Dejywan Floyd ,
George Floyd ,
Donald Trump "
Childhood Arrivals )
Joe Biden .
Vice President -
Emma Tustin ,
Arthur Labinjo -
Trade Treaty ,
Jimmy Carter .
Wasserman Schultz "
Rani Baug .
Enterprise Florida ...
West Bengal .
Cassie Compton ,
Ron DeSantis )
South Bend ,
Tana River ,
Intelligence Agency (
Breaks Down ,
Jake Angeli ,
Same Crime "
Luther King ,
Enemies Act "
Myrtle Beach ,
South Carolina ,
Ruhollah Khomeini 

NBA Finals ,
Ravi Joseph .
North Korea )
G7 Summit .
Loretta Lynch "
Hillary Clinton .
New Zealand .
Poverty Measure .
mld USD .
Janusz Piechociński (
President Trump .
Medical Research (
Matter Website ,
Act Blue '
Cortez Masto ,
Alexandria Ocasio -
Puerto Rico .
Muhammadu Buhari ,
de antifascistas&#x27 ;
Veterans Administration .
Suez Canal .
Jeeva Samadhi (
United States ,
Cannon Hinnant .
Richard Cordray "
Women Act .
Festus Keyamo ,
Sonia Gandhi “
ki Vidhwa ”
Cindy Hyde -
Baton Rouge ,
Çamlıca Mosque ,
Ghana Complex .
Tim Kaine "
National Convention .
Donald Trump "
George Floyd .
Robin Ventura .
Dream Act ,
United States ,
mente umana !
Jeffrey Epstein .
United States .
Noah Green ,
First Class ,
Lodhipur Vishnoi .
Robbie Coltrane ,
Harry Potter ,
Economic Forum (
Gregory Michael .
Barack Obama ,
Donald Trump .
Hillary Clinton "
Power Africa .
Night Live&quot ;
virus Sars -
u Washingtonu .
Alexandre Trudeau ,
Justin Trudeau ,
que RT -
Lewis Latimer ]
Bang Khae ,
Uttar Pradesh .
P

Phez Raymundo --
Indian Express ”
Patrick Morrisey "
Hurricane Dorian .
Rebecca Dallet "
Donald Trump "
President Obama .
Hurricane Maria .
Multiple Charges .
Prince Philip ‘
Hillary Clinton "
Expansion Programme (
Barack Obama .
Shri Ram ’
Dino Rossi "
Hurricane Harvey .
United States ,
World Population ,
Neil Gorsuch .
Dilma Rousseff :
Vande Mataram ,
. Omar ,
Kobe Bryant .
Joe Biden ,
United States ,
White House .
Dean Heller "
Yucca Mountain .
Melinda Gates :
Bruce Rauner .
Chuck Schumer "
Resonance Explosion !
Bakr al -
Sen. Obama .
Narendra Modi ,
Adolf Hitler .
Zhihui Hou .
Barack Obama “
Ayyappa Mala .
West Virginia )
Cardi Bee ”
Stephen Owens ,
Relief Program "
Bruce Rauner ,
West Bengal .
Jail Cell ,
Religious Freedom '
Justice Department "
Bruce Rauner ,
Madina Market .
Alexandria Ocasio -
Hillary Clinton )
Donald Trump ,
Mike Pence "
Ireland Protocol ,
Found Innocent ,
Rahat Indori .
L.A. County ,
Trade Organisation ,
Fisher Scientific ,
Health Organization (
BJP Rally ?
Ra

United States ,
South Korea ,
Ravi Verma .
Driver Licenses (
O'Hare Airport -
Medical College ,
ITF Mobile .
Dean Heller "
White House .
e Wisconsin .
Election Commission "
Jailing Hillary "
Alien Children ’
Voting Systems .
Wonder Woman ,
Henry Cavill ,
Jim Sensenbrenner "
Patriot Act .
Homeland Security (
Michael Bennet ,
Male Friends -
North Texas (
Democratic Congress (
Nana Opoku -
Instituto Butantan ]
o adenovírus ,
Sri Lanka .
Stephen Webber "
Justin Trudeau .
Flappy Bird "
Page Squeals :
Donald Trump .
Todd Rokita "
Waseem Rizvi .
polmonite batterica .
causata da …
Care Act .
Rep. Tammy "
Monica Lennon .
Finance Initiatives (
Kamala Harris "
Mount Fuji ,
Takoma Park ,
Steven Mnuchin "
Taj Hotel ,
Uttar Pradesh .
North Carolina ,
Dominic Cummings ’
Alice Cummings ,
North Carolina .
N.Y. State ‘
Assault Weapon ’
quot;a murderer&quot ;
Sambisa Forest ,
South Carolina "
Treaty Organization (
Bin Laden .
- India ,
Barack Obama .
president elect "
quot;The Simpsons&quot ;
Brahman Pie

### December 7

In [17]:
import pickle

with open ( "pos_similarities_examples.pickle", "rb" ) as f:
    idxs = pickle.load(f)

In [20]:
similarity_matrix = {}
for idx in idxs:
    similarities = syntax_similarity(trigram_map,idx)
    simple_similarities = syntax_similarity(simple_trigram_map,idx)
    weighed_similarities = [(g + h) / 2 for g, h in zip(similarities, simple_similarities)]
    similarity_matrix[idx] = weighed_similarities

In [21]:
import pickle

with open ( "similarity_matrix_rasmus.pkl", "wb" ) as f:
    pickle.dump( similarity_matrix, f )

In [22]:
with open( "pos_similarities.pickle", "rb") as f:
    birgit = pickle.load(f)

In [187]:
with open( "similarity_matrix_cpn.pkl", "rb") as f:
    eloise = pickle.load(f)

In [191]:
len(eloise)

100

In [158]:
len(sents)

47108

In [ ]:
for i in 

In [174]:
eloise[0]

[('Ratan Tata Says, If The Death Of 65 Soldiers Increases The Popularity Of A Prime Minister, Then Nobody Can Save This Country',
  0),
 ('Ratan Tata Says, If The Death Of 65 Soldiers Increases The Popularity Of A Prime Minister, Then Nobody Can Save This Country',
  0),
 ('The document that circulated did not come from the Civil Service Commission',
  1),
 ('News Outlets Did Not Report On Coronavirus Cases At Walmart, Amazon And Other Retailers',
  2),
 ('RSS built the 6000-bed COVID centre in Indore', 0),
 ('La justice belge a suspendu Covid Safe Ticket, équivalent du pass sanitaire.',
  1),
 ("New York Times used crocodile's image to say PM Narendra Modi cried", 0),
 ('A vaccine meant for cattle can be used to fight COVID-19.', 0),
 ('"My Buy America reform passed the Senate with bipartisan support. But when it got to the House, the foreign steel companies bought Washington lobbyists to kill it. [House Speaker] Paul Ryan and [Senate Majority Leader] Mitch McConnell gave them what th

In [212]:
for i, result in enumerate(sorted(eloise[93], key = lambda x: x[2], reverse=True)):
    print(i)
    print(result)

0
(20124, '‘The GDP grew from 1.91% in 2018 to 2.27% in 2019 but declined to 1.87% in the first quarter of 2020 as a result of the decline in global economic activities due to the Covid-19 pandemic’.', 24)
1
(46224, '“Last year, Democrats won nearly 50% of the vote, yet they hold only 38% of the seats in the State House and 30% of the seats in the State Senate”', 20)
2
(30782, 'In the last five years, we have built nearly 15,000 km of rural roads! 700 km of new roads have been built only in Lakhimpur.    In 70 years, Assam had seen the development of just 13,000 kms of roads in the state.', 19)
3
(32078, 'A photo depicting a man crucified and suspended from a road sign in Mexico has been shared tens of thousands of times in various contexts. The man in the photo was a suspect in a rape case in the town in Contepec, Mexico in 2012. He was kidnapped on his way to be interrogated by the police and found dead the next day, his naked body spread across a board and suspended from a road sign

(13985, 'Of all the positive Covid tests of the 9,000+ students at Cambridge University tested in the week to 6 December, every single one was found to be a false positive after a second test.', 7)
1020
(14003, '150 people killed in three days after being bitten by a butterfly with snake-head wings', 7)
1021
(14126, '"83% of Trump tax breaks go to the wealthiest 1%."', 7)
1022
(14154, 'Video of a leopard drinking water from a swimming pool of a hotel in India', 7)
1023
(14244, '"Ninety percent of people born in the 1940s ended up doing better financially than their parents. But those born in the 1980s, the much-maligned Millennials, have only a 50-50 chance of doing better (financially) than their parents, despite being the best-educated generation in our history."', 7)
1024
(14268, 'Caricature created by American cartoonist Ben Garrison, depicting the state of Indian media.', 7)
1025
(14289, 'The state of Ohio has replaced lethal injection with a head-ripping machine as a form of exec

(26742, 'India declared a public holiday for a visit from Philippine President Rodrigo Duterte?', 6)
2026
(26751, 'Supreme Court justice Ruth Bader Ginsburg advocated lowering the age of sexual consent to 12', 6)
2027
(26875, 'Proud Boys founder Gavin McInnes said inspiration for the group’s name came from “Proud of Your Boy,” a song from the stage musical &quot;Aladdin.&quot;', 6)
2028
(26883, 'Rep. Jim Jordan said "While Obama and Biden were cowering in fear on Air Force 1, Mr. Trump was on the ground with first responders searching for survivors and pulling people to safety."', 6)
2029
(26903, 'The United States imports "50 percent of at least 50 mineral commodities each year, including 100 percent of 21 of them."', 6)
2030
(26963, 'The EU imposes 50% tariffs on rice, maize and other cereals and 300% tariffs on processed sugar imported from African countries.', 6)
2031
(27030, '‘For a cumulative 29 of our 60 years of existence as a nation, we have been under military rule.’', 6)
203

(19637, 'Clouds don’t move in NASA footage of Earth rotating. This is further proof of a cloud map, used across a number of NASA images.', 5)
3171
(19710, 'Diana Spencer, Prince Harry&#039;s mother, left her son with an inheritance of around $10 million after she was killed in a car accident in 1997.', 5)
3172
(19722, 'There are small islands of fire ants floating in the floodwaters from Tropical Storm Harvey.', 5)
3173
(19725, 'A man walking his dogs in the woods in Broken Arrow, Oklahoma, stumbled upon a cage with a heavy chain and saw what he thought was a beaver. It turned out to be a dog.', 5)
3174
(19782, 'There was 90% compliance with people wearing face coverings in retail settings in Northern Ireland.', 5)
3175
(19815, '"Texas U.S. Rep John Culberson voted to let insurance companies charge people 50 and over five times more than younger people."', 5)
3176
(19866, 'An image of a highly patterned  room is a picture from the Downing Street flat refurbishment.', 5)
3177
(19884, 'T

(165, 'Trump knew the identity of the administration insider who penned an anonymous Op-Ed and book critical of the president.', 4)
4229
(167, 'Says the newly released documents underlying the FBI’s surveillance of former campaign adviser Carter Page show the Steele dossier "was responsible for starting" Special Counsel Robert Mueller’s investigation into links between the Trump campaign and Russia.', 4)
4230
(169, 'Australian philosopher Peter Singer claims that if meat consumption continues to grow, it won’t be possible to limit global warming to two degrees.', 4)
4231
(181, '312 Conservative MPs voted against forcing rented homes to be made fit for human habitation. No Labour, Liberal Democrat or SNP MPs voted against it.', 4)
4232
(199, '"The single largest expense in over half of American households is childcare."', 4)
4233
(212, 'TATA Group is celebrating its 150th anniversary, chance to win a car on the occasion.', 4)
4234
(213, 'Protest against Indian prime minister Narendra Mo

...

(35489, '"Breaking: Mike Huckabee just fired!"', 0)
42662
(35490, 'When Prime Minister Narendra Modi was not in power, he spoke about boycotting the EVM.', 0)
42663
(35491, 'An image shows a police officer in France pepper spraying a woman recently.', 0)
42664
(35492, 'Fotos muestran marchas en favor de Trump en Washington', 0)
42665
(35493, '"Proof That Trump Accuser is a Fraud…Story Came From Law and Order SVU."', 0)
42666
(35497, 'Senador tirou falas de Drauzio Varella do contexto', 0)
42667
(35498, '"The Ellen DeGeneres Show" is giving away $1,000 Amazon gift cards, PlayStation 5 consoles, and iPhones, all on Facebook.', 0)
42668
(35500, 'Work underway to rotate Big Ben so it faces Mecca', 0)
42669
(35501, 'Shiv sena goons attack IDBI Bank Manager in Maharashtra', 0)
42670
(35504, 'SFI activist Soori from JNU faked his injuries', 0)
42671
(35505, 'Netanyahu Begins Calling For Israeli Return To Ancient Homeland Of Iran', 0)
42672
(35506, 'Body becomes magnetic after COVID vaccine- N

(38241, 'COPS TAKE A KNEE THEN WALK OUT ON REDSKINS LEAVING THEM STRANDED IN THEIR LOCKER ROOM OVERNIGHT', 0)
43679
(38242, "the video shows Indonesia's Mount Semeru erupting on Dec. 4", 0)
43680
(38245, 'Viral audio claiming that steam inhalation is cure for Covid-19', 0)
43681
(38246, 'A “Center for Global Human Population Reduction” is affiliated with the Bill & Melinda Gates Foundation.', 0)
43682
(38249, 'Hyderabad BJP MLA Raja Singhs Sister Has Converted to Islam', 0)
43683
(38256, '"Hunters contribute more than $500 million" to West Virginia.', 0)
43684
(38263, 'Scuffle at Mangaluru mall due to eve-teasing of girls by &#039;peacefuls&#039;', 0)
43685
(38264, 'Thomas Binger wearing BLM pin.', 0)
43686
(38265, 'Demonstration during G7 was Satanic ritual', 0)
43687
(38269, 'Breonna Taylor was shot while in bed.', 0)
43688
(38270, 'denzel washington, ben carson endorse brain pill', 0)
43689
(38273, 'RealClearPolitics Reversed Calling Pennsylvania -- and Race -- For Biden; Rescinded 

(40805, 'Italian President Sergio Mattarella arrested for "meddling"\xa0in the 2020 US Presidential election', 0)
44633
(40806, 'Thrombosis is the leading cause of COVID-19 deaths', 0)
44634
(40808, "Kamala Harris said she believes Biden's rape accusers", 0)
44635
(40809, 'ISIS is selling Hindu girls in Kerala', 0)
44636
(40811, 'Not 17, but 4, intel agencies found Russia meddled in election.', 0)
44637
(40812, "Donald Trump said doctors had never seen a body kill coronavirus the way his body did and that when they tested his DNA it wasn't DNA but USA", 0)
44638
(40815, 'BJP leader masqueraded as Delhi police to instigate violence in farmers protest.', 0)
44639
(40816, 'former President Barack Obama was arrested for espionage on Nov. 28.', 0)
44640
(40817, 'Karnataka CM Yediyurappa announcing COVID restrictions in March 2021', 0)
44641
(40818, 'Claims that Donald Trump currently lacks a Secret Service Director, a Homeland Security Director, an ICE Director, a Secretary of Defense, a Se

(44268, 'Meat has been injected with material that makes it magnetic', 0)
45911
(44269, 'Donald Trump said the U.S. will run out of wind if it converts to wind power', 0)
45912
(44271, 'Prathap NM built his own drones and won awards for it.', 0)
45913
(44273, 'Ewedu leaves kill Coronavirus.', 0)
45914
(44276, 'Pornhub opens first SIPR website', 0)
45915
(44277, 'Rahul Gandhi offered namaz at temple in Madhya Pradesh', 0)
45916
(44282, 'Xingar o presidente é crime?', 0)
45917
(44284, 'Confirmed: 2018 Spending Bill Includes $30 Million For Paying Off Trump Mistresses', 0)
45918
(44291, 'Australian police officer brutally beaten and sexually assaulted by kangaroo', 0)
45919
(44296, 'Sainsbury’s has stopped selling fireworks due to animal welfare concerns.', 0)
45920
(44298, 'Cristiano Ronaldo Refused To Shake Hands With The President Of Israel', 0)
45921
(44300, 'UV Rays From Sunlight Kill Coronavirus', 0)
45922
(44301, 'Priorities USA on Twitter', 0)
45923
(44302, 'Image shows new WTO Di

(47061, 'VIdeo shows Rohingya Muslims in West Bengal vandalising a Hindu temple near their settlement.', 0)
46994
(47062, "South Africa's Highest Court Set To Free Continent From New World Order & Central Bank", 0)
46995
(47063, 'Dilapidated Road From Madhya Pradesh', 0)
46996
(47064, "Kejriwal offered namaz in Delhi's Jama Masjid on 1 January 2021", 0)
46997
(47073, 'Volcanic Eruption On La Palma, Canary Islands Tsunami Warning In U.S.', 0)
46998
(47074, 'cigarettes are approved by the Food and Drug Administration', 0)
46999
(47075, 'Target recently canceled its "Shop with a Cop" program because "the police ruin Target’s image."', 0)
47000
(47076, "This is Israel's air defence system in action.", 0)
47001
(47077, 'Says the GOP plan he supports is "the biggest tax cut in U.S. history."', 0)
47002
(47086, 'Right-Wing Groups Entered Shahi Idgah In Mathura', 0)
47003
(47087, 'Paul Allen To Leave $10,000 To Everyone Who Shares This Post', 0)
47004
(47088, 'Alemania, una valla separa en un 

In [27]:
import pandas as pd

sim_df = pd.DataFrame(similarity_matrix)

In [62]:
birgit_df = pd.DataFrame(birgit)

In [63]:
for col in birgit_df:
    birgit_df[col] = birgit_df[col].str[1]

In [213]:
sim_df[36208][12062]

159.0

In [215]:
sents[21368]

'"Mike Madigan made a fortune on tax appeals… Saving his friends millions... It’s an inside game played by people like Merry Marwig, Madigan’s hand-picked candidate. When Marwig thought her property taxes were too high she got them lowered at your expense. Saved so much she did it again. Marwig and Madigan: Profiting from the same corrupt system."'

In [217]:
birgit_df

46304    26590    34527    1086     8928     13250    9224     10638  \
0      39507.0  41838.5  42924.0  42694.5  28688.5  41155.5  43205.0  43407.0   
1       6247.5  18669.5  39366.0  28537.0  33194.5  12375.0  27995.0  30204.5   
2      19386.5  25835.5   7732.5  33557.5   1984.5  29178.5  38696.5  33483.0   
3        167.0   8229.5  30990.5  29582.0  27602.0  21339.5  30550.5  20224.0   
4      22509.0   1122.5   2694.0  10514.0  17016.5  11225.5  11773.0  20224.0   
...        ...      ...      ...      ...      ...      ...      ...      ...   
47103  25792.5  32775.0  28645.5  38738.5  35310.5  36995.5  41491.5  39829.5   
47104  31638.5  23764.0   5327.5   2784.0    204.5  26631.0  14913.5   9669.5   
47105  45089.5  45249.5  45462.0  45103.5  11011.5  45701.5  45353.0  44856.5   
47106  34413.0  30184.0   3060.5  24744.0  36757.5  35015.5    169.5  20224.0   
47107  20195.5  25835.5  18954.0  10514.0   7958.0  20093.5  17346.5   2413.5   

         37749    6698   ...    7915     1980     17970    36208    32851  \
0      39202.5  42663.0  ...  43100.5  38636.5  39068.0  33025.0  23288.0   
1      17623.0   8188.0  ...  30369.5  16760.0  13756.0  41277.0  28351.5   
2       7657.5  28932.0  ...  35750.0  17634.5  20577.5  23582.0  37701.0   
3       8375.5  20567.5  ...  25915.5  10690.0   8492.5  29130.5  32356.5   
4      16458.0  17951.5  ...  18060.0  10048.5   6814.5  28074.5  35684.5   
...        ...      ...  ...      ...      ...      ...      ...      ...   
47103  23977.5  38655.5  ...  37554.0  33803.5  28258.0   8642.5  26226.0   
47104  29176.0  16740.5  ...    460.0  30270.5  32160.5   5470.0   8190.5   
47105  45199.5  45164.5  ...  44786.0  44664.0  45361.0  41277.0  31300.5   
47106  33824.5  31208.5  ...  11204.5  32921.5  33297.5  23582.0  13798.5   
47107  27022.0   4547.5  ...   3899.5  29932.0  27485.5  11964.5  10731.5   

         15182    45530    24986    5224     6740   
0      42690.0  42179.0  41645.5  39145.0  39254.5  
1      25634.0   7368.5  29426.5  31356.5  14421.5  
2      32865.0  35789.0  19698.0  14931.0  23478.5  
3       9308.0   9385.0  18852.5   7123.0   7227.5  
4       7605.0  13785.5   4499.0  20209.0  15068.0  
...        ...      ...      ...      ...      ...  
47103  34897.0  39410.5  33846.5  26861.0  31355.0  
47104  13932.5  19915.0   9785.5  30269.5  33028.0  
47105  44454.5  45702.0  45168.5  45293.0  45171.0  
47106  21683.0  25596.0  29426.5  15732.5  31355.0  
47107    710.5   4393.0  22851.0  28490.0  28452.0  

[47108 rows x 100 columns]

In [71]:
for col in birgit_df:
    birgit_df[col] = birgit_df[col].rank()

In [72]:
for col in sim_df:
    sim_df[col] = sim_df[col].rank(ascending=False)

In [204]:
sents[1614]

'A post featuring a photograph of a soldier carrying a donkey on his back claims the image is from World War II and the serviceman is carrying the animal through a minefield.'

In [203]:
sents[22945]

"A video of a rainbow forming in the wake of a truck spraying moisture over a street has been viewed tens of thousands of times on Twitter and YouTube alongside a claim that the footage shows a truck disinfecting a street in China in an effort to contain the novel coronavirus. This claim is false; the video, which shows a truck spraying in China's Sichuan province for dust control purposes, has circulated online since at least March 2019, months before the viral outbreak."

In [205]:
sim_df[1614].iloc[22945]

20536.0

In [83]:
average_df = ((sim_df + birgit_df) / 2).rank()

In [138]:
birgit_df[1614].argsort()

0         1614
1        46629
2         8920
3        34480
4         8329
         ...  
47103    44673
47104    32677
47105    26312
47106     6551
47107    11295
Name: 1614, Length: 47108, dtype: int64

In [225]:
sim_df[36208].argsort()

0        36208
1        25013
2         9298
3        25050
4        21344
         ...  
47103     5806
47104    30945
47105    30944
47106    40639
47107    29298
Name: 36208, Length: 47108, dtype: int64

In [223]:
sents[37146]

'Roughly 40% of people on welfare are pensioners, and 10% or 20% are taking in-work benefits.'

In [229]:
sim_df[36208].iloc[20124]

26545.0

In [104]:
average_df

46304    26590    34527    1086     8928     13250    9224     10638  \
0      43337.0  45760.5  33260.5  35219.5  11132.0  43015.5  24105.0  42021.0   
1       1660.5  29514.0  28170.0  18231.0  38253.5  14528.0  33317.5  31213.0   
2      11526.0  35619.0   7451.5  19008.5   3025.0  11787.0  45102.0  37574.0   
3      13713.0  18534.0  35250.0  34139.0  36585.0  24831.0  35687.5  26829.0   
4      18649.5  12097.5   5287.0  12994.0  19862.0   7503.5   7305.0  12717.0   
...        ...      ...      ...      ...      ...      ...      ...      ...   
47103  18844.5  41134.5  28468.0  33623.0  34138.0  36705.5  38718.0  44604.0   
47104  29877.0   7569.0   8816.0    150.0   1259.5  35458.0  10013.0   6658.0   
47105  46289.5  41536.0  46914.5  23155.5  18185.5  46557.5  43272.5  37408.5   
47106  30377.0  11194.5   1624.5  24303.5  44524.0  44172.5     19.5  15214.0   
47107  35905.5  10168.5  30450.5  24014.5    752.5  35498.0   4635.5    376.5   

         37749    6698   ...    7915     1980     17970    36208    32851  \
0      45526.0  46378.0  ...  27682.0  39198.5  44860.5  27293.0  22814.0   
1      30931.0  22644.0  ...  41500.5   6393.5  26536.0  40323.0  16118.5   
2       7497.0  24970.5  ...  26715.0   7593.0   9324.0  15708.0  43134.0   
3       9949.0  33172.5  ...  30648.0  14819.5   3805.0  38701.0  36943.0   
4      30020.0  30936.5  ...  11211.5   5107.5  20174.0  33314.0  19357.0   
...        ...      ...  ...      ...      ...      ...      ...      ...   
47103  16426.0  36336.0  ...  33597.0  16801.5  13217.0   8738.0  38138.0   
47104  24701.0  23114.0  ...    736.0  36122.0  19630.0  14896.0  18782.0   
47105  44544.0  35513.5  ...  36532.5  45338.5  41732.0  36507.5  35803.5   
47106  39173.0  41045.0  ...  27939.5  20938.5  32395.0  25426.5  28814.5   
47107  32943.5   9158.5  ...    573.5  40779.5  37880.5  15668.5  13812.5   

         15182    45530    24986    5224     6740   
0      26160.0  31526.0  37478.0  45871.0  19940.0  
1      39185.0  11170.5  33732.0  42037.0  22525.5  
2      36010.0  44212.5  11440.0   4507.0  31525.0  
3       9415.5  11777.0  27283.5  23415.5  15443.0  
4       9697.5   9091.5  19211.0  25855.0  23179.5  
...        ...      ...      ...      ...      ...  
47103  38749.0  45544.0  24068.0  19144.5  21442.5  
47104   4043.0  13639.0  17143.0  20306.0  39254.0  
47105  32872.5  39123.5  46189.5  32243.0  37094.5  
47106   5961.5  19986.5  31035.5  16166.5  14989.5  
47107    158.5   8496.5  34630.5  16097.0  35736.5  

[47108 rows x 100 columns]

In [185]:
idxs.index(36208)

93

In [111]:
for col in average_df:
    print(col)
    print(sents[col])

46304
Aspiring astronaut Alyssa Carson is selected for a one way mission to Mars
26590
Trump says he has "recognized Russian Meddling MANY TIMES."
34527
Says Sen. Joe Manchin "stands with Hillary Clinton and D.C. Dems on gun control, higher taxes, amnesty, and Planned Parenthood."
1086
"Mass voter fraud just discovered, to the amount that could void Hillary’s victory In New Hampshire."
8928
"When two judges said it was illegal to fire a teacher" who viewed pornography at school, "Tony Evers worked with Republicans and Democrats and changed the law."
13250
Facebook user claimed that protestors were killed during Imo state protest…
9224
Says Donald Trump "games the U.S. visa system so he can hire temporary foreign workers at low wages."
10638
"Idaho mother sentenced to prison after multiple citations for breastfeeding in public."
37749
Video shows car swept down river in China's Chongqing municipality in June 2020
6698
The government reduced payments for people with disabilities by £30 a